In [3]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk import pos_tag, word_tokenize
from nltk.util import ngrams
import spacy
import time
import os

In [4]:
# Download NLTK resources (run once)
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt_tab')
nltk.download('averaged_perceptron_tagger_eng')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\reneg\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\reneg\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\reneg\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     C:\Users\reneg\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


True

In [5]:
# Download spaCy resources (run once)
nlp = spacy.load("en_core_web_trf")

In [6]:
print("Starting data preprocessing...")
start_time = time.time()

# Custom stopwords relevant to job descriptions
custom_stopwords = {'experience', 'job', 'work', 'skills', 'year', 'years', 'company',
					'team', 'role', 'ability', 'required', 'requirements', 'responsibilities',
					'candidate', 'position', 'including', 'using', 'knowledge'}

# Load the original data
jobs_associate = pd.read_csv('data/raw/Jobs_associate.csv', encoding="utf-8-sig")
jobs_director = pd.read_csv('data/raw/Jobs_director.csv', encoding="utf-8-sig")
jobs_entry_level = pd.read_csv('data/raw/Jobs_entry_level.csv', encoding="utf-8-sig")
jobs_executive = pd.read_csv('data/raw/Jobs_executive.csv', encoding="utf-8-sig")
jobs_internship_level = pd.read_csv('data/raw/Jobs_internship_level.csv', encoding="utf-8-sig")
jobs_mid_senior_level = pd.read_csv('data/raw/Jobs_mid_senior_level.csv', encoding="utf-8-sig")

# Process the original data
df = pd.concat([jobs_associate, 
						jobs_director, 
						jobs_entry_level, 
						jobs_executive, 
						jobs_internship_level,
						jobs_mid_senior_level], ignore_index=True)

# Rule 1.
# If employment_type is 'Part-time' and title contains intern-related terms and seniority is empty
internship_keywords = ['intern', 'internship', '實習']
mask_part_time = (df['employment_type'] == 'Part-time') & \
				(df['seniority'].isna() | (df['seniority'] == ''))
# Create a boolean mask for titles containing intern-related keywords
mask_intern_title = df['title'].str.lower().apply(
	lambda x: any(keyword in str(x).lower() for keyword in internship_keywords)
) if 'title' in df.columns else False
# Apply
df.loc[mask_part_time & mask_intern_title, 'seniority'] = 'Internship'

# Rule 2.
# If employment_type is 'Internship', always set seniority to 'Internship'
df.loc[df['employment_type'] == 'Internship', 'seniority'] = 'Internship'

# Rule 3
# If title contains intern-related terms and seniority is missing, fill with 'Internship'
mask_missing_seniority = df['seniority'].isna() | (df['seniority'] == '')
# Check if title contains any internship keywords
mask_intern_title = df['title'].str.lower().apply(
	lambda x: any(keyword in str(x).lower() for keyword in internship_keywords)
) if 'title' in df.columns else False
# Apply
df.loc[mask_missing_seniority & mask_intern_title, 'seniority'] = 'Internship'

# Rule 4
# For remaining missing seniority values, fill with 'Entry level'
still_missing_mask = df['seniority'].isna() | (df['seniority'] == '')
df.loc[still_missing_mask, 'seniority'] = 'Entry level'

# Rule 5
# Create a mask for rows where title contains "Error code"
mask_error_code = df['title'].str.contains("Error code", case=False, na=False)
df = df[~mask_error_code]    

# Process by category and seniority level
categories = sorted(df['category_major'].dropna().unique())

# Define seniority levels
seniority_levels = [
	'Internship',
	'Entry level', 
	'Assistant', 
	'Mid-Senior level', 
	'Director',
	'Executive (VP, GM, C-Level)',
]

# Create result dataframe
results = []

# for category in categories:
# 	print(f"Processing category: {category}")
# 	filtered_data = df[df['category_major'] == category]
	
# 	for level in seniority_levels:
# 		level_data = filtered_data[filtered_data['seniority'] == level]
		
job_description_text = " ".join(df['job_description'].fillna(''))
job_requirements_text = " ".join(df['job_requirements'].fillna(''))
skills_text = " ".join(df['skills'].fillna(''))

Starting data preprocessing...


KeyError: 'job_requirements'

Do after this line ---

In [ ]:
print(skills_text)

NameError: name 'skills_text' is not defined

In [ ]:
##########
# TODO
# Process text for 'Job Description' and 'Requirements' - 
def process_text(text, custom_stopwords=None):
    if pd.isna(text):
        return ""
    
    # Convert to lowercase and remove punctuation
    text = str(text).lower()
    text = re.sub(r'[^\w\s]', ' ', text)
    
    # Get stopwords
    stop_words = set(stopwords.words('english'))
    if custom_stopwords:
        stop_words.update(custom_stopwords)
    
    # Tokenize
    tokens = word_tokenize(text)
    
    # Initialize lemmatizer
    lemmatizer = WordNetLemmatizer()
    
    # POS tag tokens to improve lemmatization
    tagged_tokens = pos_tag(tokens)
    
    # Lemmatize words based on POS tags
    lemmatized_words = [] #['Cheical Eng', 'MBA', ]
    for word, tag in tagged_tokens:
        if word not in stop_words and len(word) > 2:
            # Convert POS tag to WordNet format
            if tag.startswith('J'):
                pos = 'a'  # adjective
            elif tag.startswith('V'):
                pos = 'v'  # verb
            elif tag.startswith('N'):
                pos = 'n'  # noun
            elif tag.startswith('R'):
                pos = 'r'  # adverb
            else:
                pos = 'n'  # default to noun
                
            lemmatized_words.append(lemmatizer.lemmatize(word, pos=pos))
    
    return " ".join(lemmatized_words)

In [ ]:
text="""National Tsing Hua University was established in Beijing in 1911 as “Tsing Hua Academy”."""

process_text(skills_text, custom_stopwords=None)

'您是否對洞察市場機會 商業模式充滿興趣 並想學習從投資人角度 輔導企業與個人成長 你是否喜歡接觸多元產業領域 站在產業趨勢最前緣 拓展自己的商業與世界認知 你是否嚮往更自由 彈性的工作模式 善於自主管理 挑戰高績效獎金 關於炙星 炙星團隊透過整合產官學研各方資源 培養具社會與商業價值的優秀團隊與人才 建構高度資源整合的新創生態系 使新世代的人才無論在當代創業或就業環境中 皆能為社會貢獻價值 創造正向循環 我們專注於投資在ai 智慧科技以及esg 綠能兩大賽道 種子輪至 pre 的新創 已投資 不同產業之新創企業 並提供完整陪跑與輔導 發掘市場領導者 炙星商業顧問扮演的角色 基於幫助潛在投資 已投資的團隊成長 炙星的商業顧問致力從 新創投資人視角 深入診斷企業 數據驅動的儀表板分析 協助企業釐清 營運流程 核心價值定位 護城河 營收增長的關鍵指標 並在產業風口來臨時 精準投資最具潛力的公司 我們不僅是顧問 更是與企業共同制定成長策略 獲取關鍵數據 調整商業模式 幫助企業加速成長的事業夥伴 炙星顧問 您將不僅提供策略建議 更會從投資人的視角透過數據與市場洞察 幫助企業優化商業模式 提升財務與營運表現 推動企業成長 透過數據驅動的儀表板 診斷企業商業模式與財務結構 找出增長關鍵指標 釐清企業營運流程 核心價值 護城河 提供具體策略與行動方案 與投資企業深度合作 掌握市場趨勢 挖掘下一個最具發展潛力轉型機會 加入我們 您會有的機會 不僅限於顧問角色 您將能學習從新創投資人視角 輔導團隊成長 並能更深入了解企業財報及商業模式輔導 透過接觸創投領域 您將有機會輔導各類新創團隊 並學習如何針對創業型公司提供策略性建議 協助新創團隊達成商業與營運優化 並在過程中積累豐富的經驗 有機會接觸到產官學研等各方知名人士及許多具有豐富經驗和專業知識的業界前輩 投資人及創業家等 透過與他們的交流和學習 可以快速拓展自我人脈並發展專業能力 提升商業思維與洞察能力 透過在專案過程中累積的顧問經驗 未來您將擁有多元的職涯選擇 擔任經理人 成為新創投資人 甚至當您未來選擇創業時 有機會獲得更多早期投資人或導師前輩的支援 環境與福利 work space 景觀舒適的工作體驗 鄰近榮星花園 綠色景觀美 交通方便 美食多 擁有團隊專屬的辦公室 亦有開放式座位區 質感沙發區等 辦公環境舒適漂亮 flexib

In [ ]:
# Process skills
def process_skills(skills_text, custom_stopwords=None):
    if pd.isna(skills_text):
        return ""
    
    # Convert to lowercase
    skills_text = str(skills_text).lower()
    
    # Split by comma
    skills = [skill.strip() for skill in skills_text.split(',')]
    
    # Get stopwords
    stop_words = set(stopwords.words('english'))
    if custom_stopwords:
        stop_words.update(custom_stopwords)
    
    # Remove stop words and filter out short skills
    skills = [skill for skill in skills if skill and skill not in stop_words and len(skill) > 2]
    
    return " ".join(skills)
##########

In [ ]:
def main():
    print("Starting data preprocessing...")
    start_time = time.time()
    
    # Custom stopwords relevant to job descriptions
    custom_stopwords = {'experience', 'job', 'work', 'skills', 'year', 'years', 'company',
                        'team', 'role', 'ability', 'required', 'requirements', 'responsibilities',
                        'candidate', 'position', 'including', 'using', 'knowledge'}
    
    # Load the original data
    jobs_associate = pd.read_csv('data/raw/Jobs_associate.csv', encoding="utf-8-sig")
    jobs_director = pd.read_csv('data/raw/Jobs_director.csv', encoding="utf-8-sig")
    jobs_entry_level = pd.read_csv('data/raw/Jobs_entry_level.csv', encoding="utf-8-sig")
    jobs_executive = pd.read_csv('data/raw/Jobs_executive.csv', encoding="utf-8-sig")
    jobs_internship_level = pd.read_csv('data/raw/Jobs_internship_level.csv', encoding="utf-8-sig")
    jobs_mid_senior_level = pd.read_csv('data/raw/Jobs_mid_senior_level.csv', encoding="utf-8-sig")

    # Process the original data
    df = pd.concat([jobs_associate, 
                            jobs_director, 
                            jobs_entry_level, 
                            jobs_executive, 
                            jobs_internship_level,
                            jobs_mid_senior_level], ignore_index=True)
    
    # Rule 1.
    # If employment_type is 'Part-time' and title contains intern-related terms and seniority is empty
    internship_keywords = ['intern', 'internship', '實習']
    mask_part_time = (df['employment_type'] == 'Part-time') & \
                    (df['seniority'].isna() | (df['seniority'] == ''))
    # Create a boolean mask for titles containing intern-related keywords
    mask_intern_title = df['title'].str.lower().apply(
        lambda x: any(keyword in str(x).lower() for keyword in internship_keywords)
    ) if 'title' in df.columns else False
    # Apply
    df.loc[mask_part_time & mask_intern_title, 'seniority'] = 'Internship'

    # Rule 2.
    # If employment_type is 'Internship', always set seniority to 'Internship'
    df.loc[df['employment_type'] == 'Internship', 'seniority'] = 'Internship'

    # Rule 3
    # If title contains intern-related terms and seniority is missing, fill with 'Internship'
    mask_missing_seniority = df['seniority'].isna() | (df['seniority'] == '')
    # Check if title contains any internship keywords
    mask_intern_title = df['title'].str.lower().apply(
        lambda x: any(keyword in str(x).lower() for keyword in internship_keywords)
    ) if 'title' in df.columns else False
    # Apply
    df.loc[mask_missing_seniority & mask_intern_title, 'seniority'] = 'Internship'

    # Rule 4
    # For remaining missing seniority values, fill with 'Entry level'
    still_missing_mask = df['seniority'].isna() | (df['seniority'] == '')
    df.loc[still_missing_mask, 'seniority'] = 'Entry level'

    # Rule 5
    # Create a mask for rows where title contains "Error code"
    mask_error_code = df['title'].str.contains("Error code", case=False, na=False)
    df = df[~mask_error_code]    
    
    # Process by category and seniority level
    categories = sorted(df['category_major'].dropna().unique())
    
    # Define seniority levels
    seniority_levels = [
        'Internship',
        'Entry level', 
        'Assistant', 
        'Mid-Senior level', 
        'Director',
        'Executive (VP, GM, C-Level)',
    ]
    
    # Create result dataframe
    results = []
    
    for category in categories:
        print(f"Processing category: {category}")
        filtered_data = df[df['category_major'] == category]
        
        for level in seniority_levels:
            level_data = filtered_data[filtered_data['seniority'] == level]
            
            if not level_data.empty:
                print(f"  - Processing {level} ({len(level_data)} jobs)")
                
                # Process skills
                processed_skills = " ".join(level_data['skills'].fillna('').apply(
                    lambda x: process_skills(x, custom_stopwords)
                ))
                
                # Process job description
                processed_description = " ".join(level_data['job_description'].fillna('').apply(
                    lambda x: process_text(x, custom_stopwords)
                ))
                
                # Process requirements
                processed_requirements = " ".join(level_data['requirements'].fillna('').apply(
                    lambda x: process_text(x, custom_stopwords)
                ))
                
                # Add to results
                results.append({
                    'category': category,
                    'seniority': level,
                    'count': len(level_data),
                    'processed_skills': processed_skills,
                    'processed_job_description': processed_description,
                    'processed_requirements': processed_requirements
                })
    
    # Create processed dataframe
    processed_df = pd.DataFrame(results)
    
    # Save to CSV
    processed_df.to_csv("data/jobs_processed.csv", index=False)
    
    elapsed_time = time.time() - start_time
    print(f"Preprocessing completed in {elapsed_time:.2f} seconds.")
    print(f"Processed data saved to data/jobs_processed.csv")

In [ ]:
if __name__ == "__main__":
    main()